# Pytorch : Distribution hybride (modèle et données) multi nœuds et multi gpu


*Notebook rédigé par l'équipe assistance IA de l'IDRIS, juin 2021*

Ce notebook met en pratique les conseils donnés dans la documentation IDRIS ([Pytorch : Distribution hybride de données et modèles multi-GPU et multi-nœuds](http://www.idris.fr/ia/hybrid-parallelism-pytorch.html)). Pour cette démonstration, nous nous limitons à un entrainement simple (sans validation) avec un modèle **resnet101** appliqué au jeu de données **Imagenet** (disponible sur **DSDIR**). 

Le procédé comprend plusieurs étapes :

* adaptation au niveau du modèle :
  * le modèle est distribué sur deux GPU ou plus
  * lors de l'entraînement, les données sont chargées sur les bons GPU, ie les GPU contenant les premières couches du modèle pour les entrées, et le GPU contenant la dernière couche pour la comparaison avec la donnée vérité (ou label)
* adaptation au niveau des données :
  * création de *dataloader* affectés aux différents processus (ou *tasks* pour reprendre le vocabulaire de Slurm)
* initialisation des codes et boucle d'entraînement sur mesure

Lors de l'adaptation de son propre code, il est conseillé de procéder par étapes, et de vérifier le bon comportement du modèle distribué (par exemple avec l'évolution de la Loss), avant d'y ajouter la distribution des données.

Ce qui suit met en avant l'expérience de l'équipe support pour mettre en place cette technique sur Jean Zay et ne se substitue pas à la documentation officielle mais la complète.

Dans la suite du notebook, **MP** (*model parallelism*) désigne la parallélisation de modèle et **DDP** (*data distribution parallelism*) désigne la distribution des données. Ceci reprend les dénominations de la documentation officielle **PyTorch**.

> Remarque : ce notebook reprend le notebook présentant la parallélisation de modèle (voir : [PyTorch : Parallélisme de modèle multi GPU](http://www.idris.fr/ia/model-parallelism-pytorch.html) pour plus d'information).

## Vérification de l'environnement

Ce notebook est prévu pour être exécuté sur une frontale de Jean-Zay (jean-zay{1-5}) et avec une version de Pytorch >= 1.8.0. Il faut donc charger préalablement cet environnement.

In [1]:
!hostname

jean-zay3


In [2]:
!module list

Currently Loaded Modulefiles:
 1) gcc/8.3.1           4) cudnn/8.0.4.30-cuda-10.2   7) openmpi/4.0.2-cuda     
 2) cuda/10.2           5) intel-mkl/2020.1           8) pytorch-gpu/py3/1.7.1  
 3) nccl/2.7.8-1-cuda   6) magma/2.5.3-cuda          
>

In [3]:
!mkdir slurm
!mkdir log
!mkdir checkpoint

mkdir: cannot create directory ‘slurm’: File exists
mkdir: cannot create directory ‘log’: File exists
mkdir: cannot create directory ‘checkpoint’: File exists


## Adaptation du modèle

Le modèle qui sert de support est Resnet101 disponible dans `torchvision`. 

Les modifications consistent :

* à répartir les différentes couches du modèle sur les GPUs disponibles puis à s'assurer de la bonne communication entre les couches (dans la fonction `forward()`, voir plus bas). Les variables `dev0` et `dev1` sont les références des GPU à utiliser. 
* à mettre en place un *pipeline*, c'est à dire à diviser le *batch* de données en plusieurs mini *batches* pour que les GPU puissent exécuter le code en parallèle (variable `split_size` et fonction `forward`)

### Création du modèle

In [4]:
%%writefile resnet.py

import torch
import torch.nn as nn
from torchvision.models.resnet import ResNet, Bottleneck

num_classes = 1000


class PipelinedResnet(ResNet):
    def __init__(self, dev0, dev1, split_size=8, *args, **kwargs):
        super(PipelinedResnet, self).__init__(
            Bottleneck, [3, 4, 23, 3], num_classes=num_classes, *args, **kwargs)
        # dev0 and dev1 point to the GPU 
        self.dev0 = dev0
        self.dev1 = dev1
        self.split_size = split_size

        self.seq0 = nn.Sequential(
            self.conv1,
            self.bn1,
            self.relu,
            self.maxpool,
            self.layer1,
            self.layer2
        ).to(self.dev0)  # sends the first sequence of the model to the first GPU

        self.seq1 = nn.Sequential(
            self.layer3,
            self.layer4,
            self.avgpool,
        ).to(self.dev1)  # sends the second sequence of the model to the second GPU

        self.fc.to(self.dev1)  # last layer is on the second GPU

Overwriting resnet.py


### Liaison entre les couches

Sans optimisation, la fonction `forward()` se résume à décrire le flux de données entre les deux GPU, depuis l'entrée `x` jusqu'à la dernière couche du modèle :
    
```py 
def forward(self, x):
    x= self.seq0(x)     # apply first sequence of the model on input x
    x= x.to(self.dev1)  # send the intermediary result to the second GPU
    x = self.seq1(x)    # apply second sequence of the model to x
    return self.fc(x.view(x.size(0), -1))
```

Le mode *pipeline* dépend de la variable `split_size` qui est à ajuster au cas par cas (idéalement via un *benchmarks* comme présenté sur la documentation officielle). Ici, nous prenons la valeur par défaut, soit 8.

In [5]:
%%writefile -a resnet.py

    def forward(self, x):
        # split setup for x, containing a batch of (image, label) as a tensor
        splits = iter(x.split(self.split_size, dim=0))
        s_next = next(splits)
        s_prev = self.seq0(s_next).to(self.dev1)
        ret = []

        for s_next in splits:
            # A. s_prev runs on dev1
            s_prev = self.seq1(s_prev)
            ret.append(self.fc(s_prev.view(s_prev.size(0), -1)))

            # B. s_next runs on dev0, which can run concurrently with A
            s_prev = self.seq0(s_next).to(self.dev1)

        s_prev = self.seq1(s_prev)
        ret.append(self.fc(s_prev.view(s_prev.size(0), -1)))

        return torch.cat(ret)

Appending to resnet.py


## Création du dataset

Nous utilisons le sous jeu de données de validation de Imagenet (`val`), qui a l'avantage de n'avoir que 50.000 échantillons, ce qui permet d'exécuter un entrainement sur plusieurs époques en quelques minutes (dans le même ordre d'idée et par soucis de concision, nous n'appliquons pas la totalité des transformations conseillées pour ce dataset). 

In [6]:
%%writefile dataset.py

import os

import idr_torch  # see http://www.idris.fr/jean-zay/gpu/jean-zay-gpu-torch-multi.html
import torch
import torchvision
import torchvision.transforms as transforms

def get_dataset(ds_name='val'):
    transform = transforms.Compose([
        transforms.RandomResizedCrop(224),  # Random resize - Data Augmentation
        transforms.ToTensor(),  # convert the PIL Image to a tensor
    ])

    train_ds = torchvision.datasets.ImageNet(root=os.environ['DSDIR'] + '/imagenet/RawImages',
                                            transform=transform,
                                            split=ds_name)  
    return train_ds


def get_ddp_loader(ds_name='val', batch_size=256, num_workers=4):
    train_ds = get_dataset(ds_name)

    num_replica = idr_torch.size
    batch_size_per_gpu = batch_size // num_replica
    train_sampler = torch.utils.data.distributed.DistributedSampler(train_ds,
                                                                    num_replicas=num_replica,
                                                                    rank=idr_torch.rank,
                                                                    shuffle=True)
    train_loader = torch.utils.data.DataLoader(dataset=train_ds,
                                               batch_size=batch_size_per_gpu,
                                               shuffle=False, num_workers=num_workers, pin_memory=True, drop_last=True,
                                               sampler=train_sampler, prefetch_factor=2)
    if idr_torch.rank == 0:
        print(f"----------\nDataset size ({ds_name}) has {len(train_ds)} training samples, num_replica sor the sampler is {idr_torch.size}")
        print(f'Global batch size: {batch_size} - mini batch size: {batch_size_per_gpu}\n----------')
    return train_loader

Overwriting dataset.py


## Code principal

Le code est volontairement verbeux avec beaucoup de `print()` pour permettre de bien comprendre quels GPU sont associés à quels processus, ainsi que la quantité de mémoire GPU utilisée. 

### Imports 

Les imports relatifs à la distribution hybride sont :

* `torch.distributed` : permet d'initaliser le code 
* `torch.nn.parallel.DistributedDataParallel` : pour la mise en place de *dataloader* multiprocess

en sus des imports spécifiques à la création du modèle et des datasets

In [7]:
%%writefile demo_mp_ddp.py

import argparse
import os
import subprocess
import time
from datetime import timedelta

import idr_torch  # see http://www.idris.fr/jean-zay/gpu/jean-zay-gpu-torch-multi.html
import torch
import torch.distributed as dist
import torch.nn as nn
from torch.nn.parallel import DistributedDataParallel

from resnet import PipelinedResnet
import dataset

Overwriting demo_mp_ddp.py


### Fonctions utiles

In [8]:
%%writefile -a demo_mp_ddp.py

def parse_args():
    parser = argparse.ArgumentParser()
    parser.add_argument('-b', '--batch-size', default=128, type=int,
                        help='batch size. it will be divided in mini-batch for each worker')
    parser.add_argument('-e', '--epochs', default=2, type=int, metavar='N',
                        help='number of total epochs to run')
    parser.add_argument('-p', '--backend', default='nccl', type=str,
                        help='choose between nccl | gloo')
    parser.add_argument('-k', '--checkpoint-path', default='checkpoint/nomodule_dist_', type=str,
                        help='relative path where model can be saved')
    parser.add_argument('-r', '--resume_model', default='', type=str,
                        help='relative path to model to load before resuming training')
    args = parser.parse_args()
    return args


def convert(seconds):
    return time.strftime("%H:%M:%S", time.gmtime(seconds))


def print_log(message):
    '''short to output messages only on first process'''
    if idr_torch.rank == 0:
        print(message)

Appending to demo_mp_ddp.py


### Setup 

Il est important de bien différencier les processus (qui vont chacun recevoir un *batch* d'échantillons) des GPUs, puisque, au contraire du mode **DDP** seul, il n'y a pas égalité entre le nombre de processus et le nombre de GPU.

Le plus important est la déclaration des GPU utilisés par le processus courant. Initialement chaque processus sur un noeud "voit" tous les GPU réservés. Il est donc important de bien affecter un couple distinct de GPU par processus.

Une limitation de pytorch + NCCL (en *backend*) oblige à ne pas affecter des GPU consécutifs par processus, c'est pourquoi nous utilisons des variables Slurm pour créer les listes de GPU.

Sur une réservation de 4 GPUs et deux tâches, les couples de GPU sont :

* 0 et 2 pour le premier processus
* 1 et 3 pour le second

Les variables `NTASKS_PER_NODE`, `hostnames` et `NODE_ID` sont issues des variables d'environnement de Slurm.

> Remarque : La limitation concernant l'affectation des GPU est valable sur le module PyTorch 1.8.0 (en avril 2021). 

In [9]:
%%writefile -a demo_mp_ddp.py

def get_model(gpu, load_model=None):
    print(f"From node_id {NODE_ID} ({hostnames[NODE_ID].decode('utf-8')}),"
          f" create model on GPUs {gpu}")
    mp_model = PipelinedResnet(gpu[0], gpu[1])
    if load_model:
        print(f"\tFrom node_id {NODE_ID} ({hostnames[NODE_ID].decode('utf-8')}),"
              f" load model on GPU {gpu} from {load_model}")
        mp_model.load_state_dict(torch.load(load_model))
    ddp_mp_model = DistributedDataParallel(mp_model)
    return ddp_mp_model

def main():
    args = parse_args()
    batch_size, epochs, checkpoint_path = args.batch_size, args.epochs, args.checkpoint_path
    if idr_torch.rank == 0:
        print(f"Current setup:")
        print(f"\tTraining on {batch_size} samples per batch, for {epochs} epoch(s).")
        print(f"\tSelected backend is: {args.backend}")

    dev0 = idr_torch.local_rank % torch.cuda.device_count()
    dev1 = dev0 + NTASKS_PER_NODE
    torch.cuda.set_device(dev0)
    gpu = [dev0, dev1]

    dist.init_process_group(backend=args.backend, timeout=timedelta(seconds=30), init_method='env://',
                            world_size=idr_torch.size, rank=idr_torch.rank)

    print(
        f"Running DDP with MP on rank {idr_torch.rank} (node {hostnames[NODE_ID].decode('utf-8')}," 
        f"current gpu is {torch.cuda.current_device()} "
        f" selected from {gpu}.")

    train_loader = dataset.get_ddp_loader(batch_size=batch_size)
    time.sleep(2)  # used only to get a clean log
    model = get_model(gpu=gpu, load_model=args.resume_model)
    time.sleep(2)  # used only to get a clean log
    training(model, train_loader, epochs, batch_size, gpu, checkpoint_path)

Appending to demo_mp_ddp.py


### Définition de la boucle d'entraînement

Les seules modifications à gérer dans cette boucle concernent la distribution de modèle : 

* les échantillons images doivent être envoyés sur le premier GPU
* les labels, quand à eux, doivent se retrouver sur le même GPU que la sortie du modèle (ie les prédictions), soit le second GPU.


La sauvegarde du modèle (dans la fonction `training`) différe de la façon de procéder en mono GPU, car l'encapsulage de modèle par la fonction `DistributedDataParallel()` ajoute un niveau de profondeur au dictionnaire des paramètres (le niveau `module`).

In [10]:
%%writefile -a demo_mp_ddp.py

def train(model, optimizer, criterion, train_loader, batch_size, gpu):
    model.train()
    if idr_torch.rank == 0:
        running_train_loss = 0.0
        running_train_corrects = 0
        start_time = time.time()
        train_time = 0
    for batch_counter, (images, labels) in enumerate(train_loader):
        images = images.to(gpu[0], non_blocking=True)
        if idr_torch.rank == 0:
            start_train_time = time.time()
        # zero the parameter gradients
        optimizer.zero_grad()
        # forward
        with torch.set_grad_enabled(True):
            outputs = model(images)
            labels = labels.to(outputs.device, non_blocking=True)
            _, preds = torch.max(outputs, 1)
            loss = criterion(outputs, labels)
            # backward + optimize only if in training phase
            loss.backward()
            optimizer.step()
        if idr_torch.rank == 0:
            # statistics
            running_train_loss += loss.item()
            running_train_corrects += torch.sum(preds == labels.data).item()
            train_time += time.time() - start_train_time
    if idr_torch.rank == 0:
        duration = time.time() - start_time
        epoch_loss = running_train_loss / (batch_counter + 1)
        epoch_acc = 100.0 * running_train_corrects / ((batch_counter + 1) * batch_size)
        print('Epoch Train Loss: {:.2f} Acc: {:.2f}'.format(epoch_loss, epoch_acc))
        
def training(model, train_loader, epochs, batch_size, gpu, checkpoint_path):
    criterion = nn.CrossEntropyLoss()
    optimizer = torch.optim.SGD(model.parameters(), 1e-3)
    scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=20, gamma=0.1)

    if idr_torch.rank == 0:
        total_time = time.time()

    for epoch in range(epochs):
        if idr_torch.rank == 0:
            print(f"Epoch {epoch + 1}/{epochs}")
            t = time.time()

        train(model, optimizer, criterion, train_loader, batch_size, gpu)
        scheduler.step()

        if idr_torch.rank == 0:
            duration = time.time() - t
            print(f"\t Duration : {duration:.2f}")
            print(f"Saving model at epoch {epoch}")
            name = f"{checkpoint_path}_{epoch}.pt"
            torch.save(model.module.state_dict(), name)

    if idr_torch.rank == 0:
        total_time_elapsed = time.time() - total_time

    if idr_torch.rank == 0:
        print("-------------------------------------")
        print(f"Total time: {total_time_elapsed:.2f} \t {convert(total_time_elapsed)}")
        print("-------------------------------------")
    time.sleep(2)  # used only to get a clean log
    for g in gpu:
        print(f"{hostnames[NODE_ID].decode('utf-8')} Device id {g} max memory usage: "
              f"{torch.cuda.max_memory_allocated(g) // (1024 * 1024)} GB")   

Appending to demo_mp_ddp.py


### Récupération des variables Slurm

Juste avant d'initialiser le modèle et de créer les dataset, on récupère les variables Slurm indispensables. Les `hostnames` et `MASTER_ADDR` servent uniquement pour les logs.

In [11]:
%%writefile -a demo_mp_ddp.py

if __name__ == '__main__':
    # get distributed configuration from Slurm environment
    NODE_ID = int(os.environ['SLURM_NODEID'])
    hostnames = subprocess.check_output(['scontrol', 'show', 'hostnames', os.environ['SLURM_JOB_NODELIST']]).split()
    MASTER_ADDR = hostnames[0].decode('utf-8')
    # only available if ntasks_per_node is defined in the slurm batch script
    NTASKS_PER_NODE = int(os.environ['SLURM_NTASKS_PER_NODE'])

    # display info
    if idr_torch.rank == 0:
        print(f"Training on {len(hostnames)} nodes and {idr_torch.size} processes, master node is {MASTER_ADDR}")
        print("Demoing ddp + model parallelism with data pipeline !")
        print(f"Variables for model parallel on one node: {torch.cuda.device_count()} accessible gpu  "
              f"and {NTASKS_PER_NODE} tasks per node declared")
    main()

Appending to demo_mp_ddp.py


## Exécution de la démo

Nous allons procéder en deux étapes, avec la même configuration (2 GPUs par modèle et 3 noeuds) :
    
* une première exécution de quelques époques avec sauvegarde du modèle à la fin de chaque époque (idéalement, il ne faudrait sauvegarder le modèle que s'il y a amélioration de la Loss) 
* une seconde exécution avec chargement d'un modèle bi gpu

Sur un noeud quadri-GPU, nous allons réserver toutes les cartes graphiques, mais ne demander que deux processus. Il est alors avantageux de prendre la totalité de la mémoire disponible, ce qui se fait via la directive `#SBATCH --cpus-per-task`. 

### Exécution du code sans récupération de modèle préentrainé

On prendra soin, dans le script Slurm, de bien définir le nombre de GPU et de tâches par noeud. 

**Rappel**:  si votre unique projet dispose d'heures CPU et GPU ou si votre login est rattaché à plusieurs projets, vous devez impérativement préciser l'attribution sur laquelle doit être décomptée les heures consommées par vos calculs, en ajoutant l'option `--account=my_project@gpu` comme indiqué dans la [documentation IDRIS](http://www.idris.fr/jean-zay/cpu/jean-zay-cpu-doc_account.html).

In [12]:
%%writefile slurm/prime_run.slurm
#!/bin/bash
#SBATCH --job-name=save
#SBATCH --output=log/prime_run.out
#SBATCH --error=log/prime_run.err
#SBATCH --gres=gpu:4
#SBATCH --nodes=3
#SBATCH --ntasks-per-node=2
#SBATCH --hint=nomultithread
#SBATCH --time=00:30:00
#SBATCH --qos=qos_gpu-dev
#SBATCH -C v100-16g
#SBATCH --cpus-per-task=20

## load Pytorch module
module purge
module load pytorch-gpu/py3/1.8.0

## launch script on every node
set -x
time srun python -u demo_mp_ddp.py -b 256 -e 2 -k "checkpoint/test_"
date

Overwriting slurm/prime_run.slurm


In [13]:
!sbatch 'slurm/prime_run.slurm'

sbatch: IDRIS: setting exclusive mode for the job.
Submitted batch job 1045332


In [14]:
import time

def check_job(name):
    sq = !squeue -u $USER -n '{name}'
    print(sq[0])
    while len(sq) >= 2:
        print(sq[1],end='\r')
        time.sleep(5)
        sq = !squeue -u $USER -n '{name}'
    print('\n Done!')

In [15]:
job_name = 'save' 
check_job(job_name)

             JOBID PARTITION     NAME     USER ST       TIME  NODES NODELIST(REASON)
           1045332   gpu_p13     save  ssos021  R       3:06      3 r13i5n[6-8]
 Done!


In [16]:
!cat "log/prime_run.err"

Loading pytorch-gpu/py3/1.8.0
  Loading requirement: gcc/8.3.1 cuda/10.2 nccl/2.8.3-1-cuda
    cudnn/8.0.4.30-cuda-10.2 intel-mkl/2020.4 magma/2.5.4-cuda
    openmpi/4.0.5-cuda
+ srun python -u demo_mp_ddp.py -b 256 -e 2 -k checkpoint/test_

real	3m4.982s
user	0m0.018s
sys	0m0.007s
+ date


In [17]:
!cat "log/prime_run.out"

Training on 3 nodes and 6 processes, master node is r13i5n6
Demoing ddp + model parallelism with data pipeline !
Variables for model parallel on one node: 4 accessible gpu  and 2 tasks per node declared
Current setup:
	Training on 256 samples per batch, for 2 epoch(s).
	Selected backend is: nccl
Running DDP with MP on rank 0 (node r13i5n6,current gpu is 0  selected from [0, 2].
Running DDP with MP on rank 2 (node r13i5n7,current gpu is 0  selected from [0, 2].
Running DDP with MP on rank 1 (node r13i5n6,current gpu is 1  selected from [1, 3].
Running DDP with MP on rank 5 (node r13i5n8,current gpu is 1  selected from [1, 3].
Running DDP with MP on rank 3 (node r13i5n7,current gpu is 1  selected from [1, 3].
Running DDP with MP on rank 4 (node r13i5n8,current gpu is 0  selected from [0, 2].
----------
Dataset size (val) has 50000 training samples, num_replica sor the sampler is 6
Global batch size: 256 - mini batch size: 42
----------
From node_id 0 (r13i5n6), create model on GPUs [0, 2

### Exécution du code avec chargement de modèle avant de commencer l'entraînement

Le modèle précédemment créé lors de la première époque sera chargé lors de la création du modèle. 

In [18]:
!ls "checkpoint"

test__0.pt  test__1.pt


In [19]:
%%writefile slurm/second_run.slurm
#!/bin/bash
#SBATCH --job-name=load
#SBATCH --output=log/second_run.out
#SBATCH --error=log/second_run.err
#SBATCH --gres=gpu:4
#SBATCH --nodes=3
#SBATCH --ntasks-per-node=2
#SBATCH --hint=nomultithread
#SBATCH --time=00:30:00
#SBATCH --qos=qos_gpu-dev
#SBATCH -C v100-16g
#SBATCH --cpus-per-task=20


## load Pytorch module
module purge
module load pytorch-gpu/py3/1.8.0

## launch script on every node
set -x
time srun python -u demo_mp_ddp.py -b 256 -e 2 -k "checkpoint/check_" -r "checkpoint/test__1.pt"
date

Overwriting slurm/second_run.slurm


In [20]:
!sbatch 'slurm/second_run.slurm'

sbatch: IDRIS: setting exclusive mode for the job.
Submitted batch job 1045423


In [21]:
job_name = 'load' 
check_job(job_name)

             JOBID PARTITION     NAME     USER ST       TIME  NODES NODELIST(REASON)
           1045423   gpu_p13     load  ssos021  R       2:54      3 r13i5n[6-8]
 Done!


In [22]:
!cat "log/second_run.err"

Loading pytorch-gpu/py3/1.8.0
  Loading requirement: gcc/8.3.1 cuda/10.2 nccl/2.8.3-1-cuda
    cudnn/8.0.4.30-cuda-10.2 intel-mkl/2020.4 magma/2.5.4-cuda
    openmpi/4.0.5-cuda
+ srun python -u demo_mp_ddp.py -b 256 -e 2 -k checkpoint/check_ -r checkpoint/test__1.pt

real	2m57.146s
user	0m0.016s
sys	0m0.009s
+ date


In [23]:
!cat "log/second_run.out"

Training on 3 nodes and 6 processes, master node is r13i5n6
Demoing ddp + model parallelism with data pipeline !
Variables for model parallel on one node: 4 accessible gpu  and 2 tasks per node declared
Current setup:
	Training on 256 samples per batch, for 2 epoch(s).
	Selected backend is: nccl
Running DDP with MP on rank 0 (node r13i5n6,current gpu is 0  selected from [0, 2].
Running DDP with MP on rank 2 (node r13i5n7,current gpu is 0  selected from [0, 2].
Running DDP with MP on rank 4 (node r13i5n8,current gpu is 0  selected from [0, 2].
Running DDP with MP on rank 1 (node r13i5n6,current gpu is 1  selected from [1, 3].
Running DDP with MP on rank 3 (node r13i5n7,current gpu is 1  selected from [1, 3].
Running DDP with MP on rank 5 (node r13i5n8,current gpu is 1  selected from [1, 3].
----------
Dataset size (val) has 50000 training samples, num_replica sor the sampler is 6
Global batch size: 256 - mini batch size: 42
----------
From node_id 1 (r13i5n7), create model on GPUs [0, 2